In [1]:
import pandas as pd
import backtesting
# from backtesting import Backtest, Strategy
from backtesting.lib import SignalStrategy, TrailingStrategy
from backtesting import *
import numpy as np
from datetime import timedelta
import warnings
warnings.filterwarnings("ignore")

import ipywidgets as widgets

C:\Users\Karolina\anaconda3\envs\Magisterka\lib\site-packages\backtesting\_plotting.py:50: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support (e.g. PyCharm, Spyder IDE). Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


Loading BokehJS ...

In [2]:
data = pd.read_csv('data/decisions_EURUSD_4H.csv')

In [3]:
data.head(10)

id    name     Open    Close     High      Low  data_volume   
0  52975  EURUSD  1.06110  1.06234  1.06291  1.05905          0.0  \
1  52976  EURUSD  1.06238  1.05525  1.06260  1.05515          0.0   
2  52977  EURUSD  1.05526  1.05300  1.05676  1.05151          0.0   
3  52978  EURUSD  1.05302  1.05217  1.05433  1.05157          0.0   
4  52979  EURUSD  1.05225  1.05253  1.05328  1.05187          0.0   
5  52980  EURUSD  1.05252  1.05146  1.05366  1.05110          0.0   
6  52981  EURUSD  1.05150  1.05075  1.05310  1.04966          0.0   
7  52982  EURUSD  1.05076  1.05427  1.05452  1.04825          0.0   
8  52983  EURUSD  1.05425  1.06376  1.06381  1.05012          0.0   
9  52984  EURUSD  1.06377  1.06437  1.06481  1.06296          0.0   

             data_datetime timeframe    Name  ...  MACD_decision  diff_MACD   
0  2023-01-05 06:00:00.000        4h  EURUSD  ...              0   0.000127  \
1  2023-01-05 10:00:00.000        4h  EURUSD  ...             -1  -0.000253   
2  2023-01-05 14:00:00.000        4h  EURUSD  ...              0  -0.000623   
3  2023-01-05 18:00:00.000        4h  EURUSD  ...              0  -0.000875   
4  2023-01-05 22:00:00.000        4h  EURUSD  ...              0  -0.000961   
5  2023-01-06 02:00:00.000        4h  EURUSD  ...              0  -0.001028   
6  2023-01-06 06:00:00.000        4h  EURUSD  ...              0  -0.001055   
7  2023-01-06 10:00:00.000        4h  EURUSD  ...              0  -0.000782   
8  2023-01-06 14:00:00.000        4h  EURUSD  ...              1   0.000047   
9  2023-01-06 18:00:00.000        4h  EURUSD  ...              0   0.000614   

   diff_MACD_prev  fuzz_MACD_strategy  dec_bollinger  diff_cl_BU  diff_cl_BL   
0        0.000000                   0              0   -0.010100    0.010609  \
1        0.000127                   0              0   -0.016213    0.004001   
2       -0.000253                   0              0   -0.017479    0.002439   
3       -0.000623                   0              0   -0.017555    0.002427   
4       -0.000875                   0              0   -0.016147    0.003274   
5       -0.000961                   0              0   -0.016441    0.002886   
6       -0.001028                   0              0   -0.016215    0.002765   
7       -0.001055                   0              0   -0.011303    0.006067   
8       -0.000782                   1              0   -0.001144    0.015149   
9        0.000047                   0              0   -0.001629    0.015895   

   prev_diff_cl_BU  prev_diff_cl_BL  fuzz_BB_strategy  
0        -0.011344         0.009795                 0  
1        -0.010100         0.010609                 0  
2        -0.016213         0.004001                 0  
3        -0.017479         0.002439                 0  
4        -0.017555         0.002427                 0  
5        -0.016147         0.003274                 0  
6        -0.016441         0.002886                 0  
7        -0.016215         0.002765                 0  
8        -0.011303         0.006067                 0  
9        -0.001144         0.015149                 0  

[10 rows x 50 columns]

In [4]:
data.columns.tolist()

['id',
 'name',
 'Open',
 'Close',
 'High',
 'Low',
 'data_volume',
 'data_datetime',
 'timeframe',
 'Name',
 'Return',
 'Up',
 'Down',
 'avg_14up',
 'avg_14down',
 'RS_14',
 'RSI',
 '5MA',
 '15MA',
 '12Ewm',
 '26Ewm',
 'MACD',
 'low_14',
 'high_14',
 'k_percent',
 'r_percent',
 'B_MA',
 'BU',
 'BL',
 'dec_rsi',
 'Signal_RSI_fuzz_system',
 'dec_will',
 'Signal_william_fuzz_system',
 'prev_5MA',
 'crossover',
 'cross_MA',
 'diff_MA',
 'diff_MA_prev',
 'fuzz_MA_strategy',
 'Signal_Line',
 'MACD_decision',
 'diff_MACD',
 'diff_MACD_prev',
 'fuzz_MACD_strategy',
 'dec_bollinger',
 'diff_cl_BU',
 'diff_cl_BL',
 'prev_diff_cl_BU',
 'prev_diff_cl_BL',
 'fuzz_BB_strategy']

### Sprawdzanie sygnałów w kolumnach ostrych i rozmytych

In [4]:
# Zliczenie przypadków, w których wartości są przeciwne

rsi_count = ((data['dec_rsi'] == 1) & (data['Signal_RSI_fuzz_system'] == -1) | (data['dec_rsi'] == -1) & (data['Signal_RSI_fuzz_system'] == 1)).sum()
print("rsi_count", rsi_count)

williams_count = ((data['dec_will'] == 1) & (data['Signal_william_fuzz_system'] == -1) | (data['dec_will'] == -1) & (data['Signal_william_fuzz_system'] == 1)).sum()
print("williams_count", williams_count)

# cross_MA - ostre decyzje
ma_count = ((data['cross_MA'] == 1) & (data['fuzz_MA_strategy'] == -1) | (data['cross_MA'] == -1) & (data['fuzz_MA_strategy'] == 1)).sum()
print("ma_count", ma_count)

macd_count = ((data['MACD_decision'] == 1) & (data['fuzz_MACD_strategy'] == -1) | (data['MACD_decision'] == -1) & (data['fuzz_MACD_strategy'] == 1)).sum()
print("macd_count", macd_count)


bb_count = ((data['dec_bollinger'] == 1) & (data['fuzz_BB_strategy'] == -1) | (data['dec_bollinger'] == -1) & (data['fuzz_BB_strategy'] == 1)).sum()

print("bb_count", bb_count)


rsi_count 0
williams_count 0
ma_count 0
macd_count 0
bb_count 0


In [4]:
data = data.set_index(pd.DatetimeIndex(data['data_datetime']))

In [7]:
data.head()

id    name     Open    Close     High      Low   
data_datetime                                                            
2023-01-05 06:00:00  52975  EURUSD  1.06110  1.06234  1.06291  1.05905  \
2023-01-05 10:00:00  52976  EURUSD  1.06238  1.05525  1.06260  1.05515   
2023-01-05 14:00:00  52977  EURUSD  1.05526  1.05300  1.05676  1.05151   
2023-01-05 18:00:00  52978  EURUSD  1.05302  1.05217  1.05433  1.05157   
2023-01-05 22:00:00  52979  EURUSD  1.05225  1.05253  1.05328  1.05187   

                     data_volume            data_datetime timeframe    Name   
data_datetime                                                                 
2023-01-05 06:00:00          0.0  2023-01-05 06:00:00.000        4h  EURUSD  \
2023-01-05 10:00:00          0.0  2023-01-05 10:00:00.000        4h  EURUSD   
2023-01-05 14:00:00          0.0  2023-01-05 14:00:00.000        4h  EURUSD   
2023-01-05 18:00:00          0.0  2023-01-05 18:00:00.000        4h  EURUSD   
2023-01-05 22:00:00          0.0  2023-01-05 22:00:00.000        4h  EURUSD   

                     ...  MACD_decision  diff_MACD  diff_MACD_prev   
data_datetime        ...                                             
2023-01-05 06:00:00  ...              0   0.000127        0.000000  \
2023-01-05 10:00:00  ...             -1  -0.000253        0.000127   
2023-01-05 14:00:00  ...              0  -0.000623       -0.000253   
2023-01-05 18:00:00  ...              0  -0.000875       -0.000623   
2023-01-05 22:00:00  ...              0  -0.000961       -0.000875   

                     fuzz_MACD_strategy  dec_bollinger  diff_cl_BU   
data_datetime                                                        
2023-01-05 06:00:00                   0              0   -0.010100  \
2023-01-05 10:00:00                   0              0   -0.016213   
2023-01-05 14:00:00                   0              0   -0.017479   
2023-01-05 18:00:00                   0              0   -0.017555   
2023-01-05 22:00:00                   0              0   -0.016147   

                     diff_cl_BL  prev_diff_cl_BU  prev_diff_cl_BL   
data_datetime                                                       
2023-01-05 06:00:00    0.010609        -0.011344         0.009795  \
2023-01-05 10:00:00    0.004001        -0.010100         0.010609   
2023-01-05 14:00:00    0.002439        -0.016213         0.004001   
2023-01-05 18:00:00    0.002427        -0.017479         0.002439   
2023-01-05 22:00:00    0.003274        -0.017555         0.002427   

                     fuzz_BB_strategy  
data_datetime                          
2023-01-05 06:00:00                 0  
2023-01-05 10:00:00                 0  
2023-01-05 14:00:00                 0  
2023-01-05 18:00:00                 0  
2023-01-05 22:00:00                 0  

[5 rows x 50 columns]

## Tylko sygnały

### Ostre

In [10]:
class CustomStrategy(SignalStrategy):
    def init(self):
        super().init()
        
        self.set_signal(data['dec_rsi'])
      
        
bt = Backtest(data, CustomStrategy, cash=10000, 
              commission=0.002, trade_on_close=False, hedging = False, exclusive_orders = True)

stats = bt.run()
bt.plot()
stats

Start                     2023-01-05 09:00:00
End                       2023-11-21 11:00:00
Duration                    320 days 02:00:00
Exposure Time [%]                    99.81125
Equity Final [$]                  9997.458813
Equity Peak [$]                  10000.001422
Return [%]                          -0.025412
Buy & Hold Return [%]                1.754957
Return (Ann.) [%]                   -0.023895
Volatility (Ann.) [%]                0.001842
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                   -0.025428
Avg. Drawdown [%]                    -0.01272
Max. Drawdown Duration      309 days 03:00:00
Avg. Drawdown Duration      154 days 15:00:00
# Trades                                 1167
Win Rate [%]                         7.540703
Best Trade [%]                        0.75084
Worst Trade [%]                     -1.520596
Avg. Trade [%]                    

### Rozmyte

In [11]:
class CustomStrategy(SignalStrategy):
    def init(self):
        super().init()
        
        self.set_signal(data['Signal_RSI_fuzz_system'])
      
        
bt = Backtest(data, CustomStrategy, cash=10000, 
              commission=0.002, trade_on_close=False, hedging = False, exclusive_orders = True)

stats = bt.run()
bt.plot()
stats

Start                     2023-01-05 09:00:00
End                       2023-11-21 11:00:00
Duration                    320 days 02:00:00
Exposure Time [%]                   99.830125
Equity Final [$]                  9996.816688
Equity Peak [$]                   10000.00135
Return [%]                          -0.031833
Buy & Hold Return [%]                1.754957
Return (Ann.) [%]                   -0.029933
Volatility (Ann.) [%]                0.002019
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                   -0.031848
Avg. Drawdown [%]                   -0.015931
Max. Drawdown Duration      309 days 03:00:00
Avg. Drawdown Duration      154 days 15:00:00
# Trades                                 1461
Win Rate [%]                         7.049966
Best Trade [%]                        1.19933
Worst Trade [%]                     -1.486818
Avg. Trade [%]                    

## Strategia z tp i sl

	tp	sl	size
	0,046	0,074	0,99
	0,076	0,087	0,98
	0,079	0,054	0,42
	0,099	0,09	0,42
	0,031	0,01	0,99
	0,046	0,069	0,92
	0,012	0,011	0,99
	0,069	0,056	0,99
	0,022	0,021	0,61
	0,034	0,024	0,99
średnia	0,0514	0,0496	0,83

### Ostre

In [18]:
class CustomStrategy(SignalStrategy):
    
    ssl = 0.0496
    ttp = 0.0514
    size_tr = 0.83
    def init(self):
        
        super().init()
        self.rsi = self.I(lambda x: data['dec_rsi'], 'rsi')

    def next(self):
        
        close = self.data.Close
        signal = self.rsi
        #prev_signal = self.rsi[-1]
        
        upper_tp = close*(1+self.ttp) 
        upper_sl = close*(1+self.ssl) 
        lower_sl = close*(1-self.ssl)   
        lower_tp = close*(1-self.ttp)
        
        #size_transaction = 0.85
        
        #if not signal == prev_signal:
        if signal == 1 and not self.position.is_long:
            self.buy(size=self.size_tr, sl=lower_sl, tp=upper_tp)
        elif signal == -1 and not self.position.is_short:
            self.sell(size=self.size_tr, sl = upper_sl, tp=lower_tp)
                
bt = Backtest(data, CustomStrategy, cash=10000, commission=0.002, 
              trade_on_close=False, hedging=False)
stats = bt.run()
bt.plot()
stats

#optymalizacja parametrow
# stats_skopt, heatmap, optimize_result = bt.optimize(ttp=[0.01, 0.1],
#            ssl=[0.01, 0.1],
#            size_tr=[0.4, 1], 
#            maximize='Equity Final [$]',
#            method='skopt',
#            max_tries=1000,
#            random_state=10,
#            return_heatmap=True,
#            return_optimization=True)
# heatmap.sort_values().iloc[-3:]

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   98.609904
Equity Final [$]                  8712.854077
Equity Peak [$]                  10005.646661
Return [%]                         -12.871459
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                  -13.956022
Volatility (Ann.) [%]                3.471128
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                  -14.009948
Avg. Drawdown [%]                    -7.07112
Max. Drawdown Duration      262 days 07:00:00
Avg. Drawdown Duration      131 days 14:00:00
# Trades                                   47
Win Rate [%]                        17.021277
Best Trade [%]                       1.334976
Worst Trade [%]                     -3.047905
Avg. Trade [%]                    

In [9]:
stats_skopt

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   98.609904
Equity Final [$]                  9927.053398
Equity Peak [$]                  10064.386579
Return [%]                          -0.729466
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                   -0.795517
Volatility (Ann.) [%]                6.554967
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                   -7.600937
Avg. Drawdown [%]                   -1.598795
Max. Drawdown Duration      224 days 11:00:00
Avg. Drawdown Duration       32 days 20:00:00
# Trades                                   12
Win Rate [%]                             50.0
Best Trade [%]                       0.602105
Worst Trade [%]                     -1.221576
Avg. Trade [%]                    

### Rozmyte

In [19]:
class CustomStrategy(SignalStrategy):
    
    ssl = 0.0496
    ttp = 0.0514
    size_tr = 0.83
    def init(self):
        
        super().init()
        self.rsi = self.I(lambda x: data['Signal_RSI_fuzz_system'], 'rsi')

    def next(self):
        
        close = self.data.Close
        signal = self.rsi
        #prev_signal = self.rsi[-1]
        
        upper_tp = close*(1+self.ttp) 
        upper_sl = close*(1+self.ssl) 
        lower_sl = close*(1-self.ssl)   
        lower_tp = close*(1-self.ttp)
        
        #size_transaction = 0.85
        
        #if not signal == prev_signal:
        if signal == 1 and not self.position.is_long:
            self.buy(size=self.size_tr, sl=lower_sl, tp=upper_tp)
        elif signal == -1 and not self.position.is_short:
            self.sell(size=self.size_tr, sl = upper_sl, tp=lower_tp)
                
bt = Backtest(data, CustomStrategy, cash=10000, commission=0.002, 
              trade_on_close=False, hedging=False)
stats = bt.run()
bt.plot()
stats

#optymalizacja parametrow
# stats_skopt, heatmap, optimize_result = bt.optimize(ttp=[0.01, 0.1],
#            ssl=[0.01, 0.1],
#            size_tr=[0.4, 1], 
#            maximize='Equity Final [$]',
#            method='skopt',
#            max_tries=1000,
#            random_state=10,
#            return_heatmap=True,
#            return_optimization=True)
# heatmap.sort_values().iloc[-3:]

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   99.739357
Equity Final [$]                  9142.484177
Equity Peak [$]                  10135.262129
Return [%]                          -8.575158
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                   -9.317267
Volatility (Ann.) [%]                2.844126
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                  -10.548029
Avg. Drawdown [%]                   -3.702201
Max. Drawdown Duration      263 days 03:00:00
Avg. Drawdown Duration       88 days 05:00:00
# Trades                                   44
Win Rate [%]                        27.272727
Best Trade [%]                       1.671077
Worst Trade [%]                      -3.60883
Avg. Trade [%]                    

In [11]:
stats_skopt

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   99.739357
Equity Final [$]                  9907.405334
Equity Peak [$]                  10164.643941
Return [%]                          -0.925947
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                   -1.009697
Volatility (Ann.) [%]                6.254074
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                   -8.724831
Avg. Drawdown [%]                   -3.129908
Max. Drawdown Duration      263 days 03:00:00
Avg. Drawdown Duration       88 days 05:00:00
# Trades                                   14
Win Rate [%]                             50.0
Best Trade [%]                       1.671077
Worst Trade [%]                     -3.173552
Avg. Trade [%]                    

***
***

## Williams %R

### Ostre

In [21]:
class CustomStrategy(SignalStrategy):
    ssl = 0.0496
    ttp = 0.0514
    size_tr = 0.83
    def init(self):
        
        super().init()
        self.rsi = self.I(lambda x: data['dec_will'], 'williams')

    def next(self):
        
        close = self.data.Close
        signal = self.rsi
        #prev_signal = self.rsi[-1]
        
        upper_tp = close*(1+self.ttp) 
        upper_sl = close*(1+self.ssl) 
        lower_sl = close*(1-self.ssl)   
        lower_tp = close*(1-self.ttp)
        
        #size_transaction = 0.85
        
        #if not signal == prev_signal:
        if signal == 1 and not self.position.is_long:
            self.buy(size=self.size_tr, sl=lower_sl, tp=upper_tp)
        elif signal == -1 and not self.position.is_short:
            self.sell(size=self.size_tr, sl = upper_sl, tp=lower_tp)
                
bt = Backtest(data, CustomStrategy, cash=10000, commission=0.002, 
              trade_on_close=False, hedging=False)
stats = bt.run()
bt.plot()
stats

#optymalizacja parametrow
# stats_skopt, heatmap, optimize_result = bt.optimize(ttp=[0.01, 0.1],
#            ssl=[0.01, 0.1],
#            size_tr=[0.4, 1], 
#            maximize='Equity Final [$]',
#            method='skopt',
#            max_tries=1000,
#            random_state=10,
#            return_heatmap=True,
#            return_optimization=True)
# heatmap.sort_values().iloc[-3:]

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   99.739357
Equity Final [$]                    8976.1929
Equity Peak [$]                  10039.907599
Return [%]                         -10.238071
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                  -11.115132
Volatility (Ann.) [%]                2.938154
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                  -10.721457
Avg. Drawdown [%]                   -5.620551
Max. Drawdown Duration      265 days 23:00:00
Avg. Drawdown Duration      133 days 14:00:00
# Trades                                   88
Win Rate [%]                        21.590909
Best Trade [%]                       0.745798
Worst Trade [%]                      -2.60455
Avg. Trade [%]                    

In [13]:
stats_skopt

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   99.739357
Equity Final [$]                  9661.183633
Equity Peak [$]                  10003.568273
Return [%]                          -3.388164
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                   -3.690427
Volatility (Ann.) [%]                 1.37374
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                   -3.607411
Avg. Drawdown [%]                   -1.936546
Max. Drawdown Duration      266 days 03:00:00
Avg. Drawdown Duration      133 days 16:00:00
# Trades                                   71
Win Rate [%]                        26.760563
Best Trade [%]                       1.757947
Worst Trade [%]                      -2.60455
Avg. Trade [%]                    

### Rozmyte

In [22]:
class CustomStrategy(SignalStrategy):
    
    ssl = 0.0496
    ttp = 0.0514
    size_tr = 0.83
    def init(self):
        
        super().init()
        self.rsi = self.I(lambda x: data['Signal_william_fuzz_system'], 'williams')

    def next(self):
        
        close = self.data.Close
        signal = self.rsi
        #prev_signal = self.rsi[-1]
        
        upper_tp = close*(1+self.ttp) 
        upper_sl = close*(1+self.ssl) 
        lower_sl = close*(1-self.ssl)   
        lower_tp = close*(1-self.ttp)
        
        #size_transaction = 0.85
        
        #if not signal == prev_signal:
        if signal == 1 and not self.position.is_long:
            self.buy(size=self.size_tr, sl=lower_sl, tp=upper_tp)
        elif signal == -1 and not self.position.is_short:
            self.sell(size=self.size_tr, sl = upper_sl, tp=lower_tp)
                
bt = Backtest(data, CustomStrategy, cash=10000, commission=0.002, 
              trade_on_close=False, hedging=False)
stats = bt.run()
bt.plot()
stats

#optymalizacja parametrow
# stats_skopt, heatmap, optimize_result = bt.optimize(ttp=[0.01, 0.1],
#            ssl=[0.01, 0.1],
#            size_tr=[0.4, 1], 
#            maximize='Equity Final [$]',
#            method='skopt',
#            max_tries=1000,
#            random_state=10,
#            return_heatmap=True,
#            return_optimization=True)
# heatmap.sort_values().iloc[-3:]

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   99.826238
Equity Final [$]                  8693.043926
Equity Peak [$]                       10000.0
Return [%]                         -13.069561
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                  -14.169421
Volatility (Ann.) [%]                2.750668
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                  -13.451478
Avg. Drawdown [%]                  -13.451478
Max. Drawdown Duration      267 days 11:00:00
Avg. Drawdown Duration      267 days 11:00:00
# Trades                                  108
Win Rate [%]                        17.592593
Best Trade [%]                       0.620961
Worst Trade [%]                     -2.758101
Avg. Trade [%]                    

In [15]:
stats_skopt

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   99.826238
Equity Final [$]                  9507.985994
Equity Peak [$]                       10000.0
Return [%]                           -4.92014
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                   -5.355238
Volatility (Ann.) [%]                1.511112
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                   -5.223057
Avg. Drawdown [%]                   -5.223057
Max. Drawdown Duration      267 days 11:00:00
Avg. Drawdown Duration      267 days 11:00:00
# Trades                                   93
Win Rate [%]                        25.806452
Best Trade [%]                       2.079661
Worst Trade [%]                     -2.377701
Avg. Trade [%]                    

## MA

### Ostre

In [7]:

class CustomStrategy(SignalStrategy):
    
    ssl = 0.012082
    ttp = 0.031785
    size_tr = 0.999022
    def init(self):
        
        super().init()
        self.rsi = self.I(lambda x: data['cross_MA'], 'ma')

    def next(self):
        
        close = self.data.Close
        signal = self.rsi
        #prev_signal = self.rsi[-1]
        
        upper_tp = close*(1+self.ttp) 
        upper_sl = close*(1+self.ssl) 
        lower_sl = close*(1-self.ssl)   
        lower_tp = close*(1-self.ttp)
        
        #size_transaction = 0.85
        
        #if not signal == prev_signal:
        if signal == 1 and not self.position.is_long:
            self.buy(size=self.size_tr, sl=lower_sl, tp=upper_tp)
        elif signal == -1 and not self.position.is_short:
            self.sell(size=self.size_tr, sl = upper_sl, tp=lower_tp)
                
bt = Backtest(data, CustomStrategy, cash=10000, commission=0.002, 
              trade_on_close=False, hedging=False)
stats = bt.run()
bt.plot()
stats

# #optymalizacja parametrow
# stats_skopt, heatmap, optimize_result = bt.optimize(ttp=[0.01, 0.1],
#            ssl=[0.01, 0.1],
#            size_tr=[0.4, 1], 
#            maximize='Equity Final [$]',
#            method='skopt',
#            max_tries=1000,
#            random_state=10,
#            return_heatmap=True,
#            return_optimization=True)
# heatmap.sort_values().iloc[-3:]

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   97.393571
Equity Final [$]                 11284.532394
Equity Peak [$]                  11357.340314
Return [%]                          12.845324
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                   14.091897
Volatility (Ann.) [%]                6.147685
Sharpe Ratio                         2.292228
Sortino Ratio                        4.172139
Calmar Ratio                         6.656799
Max. Drawdown [%]                   -2.116918
Avg. Drawdown [%]                    -0.42701
Max. Drawdown Duration       40 days 12:00:00
Avg. Drawdown Duration        4 days 10:00:00
# Trades                                   53
Win Rate [%]                        83.018868
Best Trade [%]                       3.003523
Worst Trade [%]                     -1.409937
Avg. Trade [%]                    

In [17]:
stats_skopt

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   97.393571
Equity Final [$]                 11284.539848
Equity Peak [$]                  11357.347768
Return [%]                          12.845398
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                   14.091979
Volatility (Ann.) [%]                6.147694
Sharpe Ratio                         2.292238
Sortino Ratio                        4.172166
Calmar Ratio                          6.65686
Max. Drawdown [%]                   -2.116911
Avg. Drawdown [%]                   -0.427009
Max. Drawdown Duration       40 days 12:00:00
Avg. Drawdown Duration        4 days 10:00:00
# Trades                                   53
Win Rate [%]                        83.018868
Best Trade [%]                       3.003558
Worst Trade [%]                     -1.409931
Avg. Trade [%]                    

### Rozmyte

In [24]:
class CustomStrategy(SignalStrategy):
    
    ssl = 0.0496
    ttp = 0.0514
    size_tr = 0.83
    def init(self):
        
        super().init()
        self.rsi = self.I(lambda x: data['fuzz_MA_strategy'], 'ma')

    def next(self):
        
        close = self.data.Close
        signal = self.rsi
        #prev_signal = self.rsi[-1]
        
        upper_tp = close*(1+self.ttp) 
        upper_sl = close*(1+self.ssl) 
        lower_sl = close*(1-self.ssl)   
        lower_tp = close*(1-self.ttp)
        
        #size_transaction = 0.85
        
        #if not signal == prev_signal:
        if signal == 1 and not self.position.is_long:
            self.buy(size=self.size_tr, sl=lower_sl, tp=upper_tp)
        elif signal == -1 and not self.position.is_short:
            self.sell(size=self.size_tr, sl = upper_sl, tp=lower_tp)
                
bt = Backtest(data, CustomStrategy, cash=10000, commission=0.002, 
              trade_on_close=False, hedging=False)
stats = bt.run()
bt.plot()
stats

#optymalizacja parametrow
# stats_skopt, heatmap, optimize_result = bt.optimize(ttp=[0.01, 0.1],
#            ssl=[0.01, 0.1],
#            size_tr=[0.4, 1], 
#            maximize='Equity Final [$]',
#            method='skopt',
#            max_tries=1000,
#            random_state=10,
#            return_heatmap=True,
#            return_optimization=True)
# heatmap.sort_values().iloc[-3:]

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   99.739357
Equity Final [$]                 10030.095046
Equity Peak [$]                  10061.533865
Return [%]                            0.30095
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                    0.328354
Volatility (Ann.) [%]                3.625554
Sharpe Ratio                         0.090567
Sortino Ratio                         0.12386
Calmar Ratio                         0.095896
Max. Drawdown [%]                    -3.42407
Avg. Drawdown [%]                   -0.675228
Max. Drawdown Duration      187 days 07:00:00
Avg. Drawdown Duration       38 days 00:00:00
# Trades                                   23
Win Rate [%]                        47.826087
Best Trade [%]                       4.147581
Worst Trade [%]                       -3.0582
Avg. Trade [%]                    

In [19]:
stats_skopt

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                    91.92007
Equity Final [$]                 10894.723482
Equity Peak [$]                  10894.723482
Return [%]                           8.947235
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                    9.799283
Volatility (Ann.) [%]                5.359197
Sharpe Ratio                         1.828498
Sortino Ratio                        2.959562
Calmar Ratio                         2.564575
Max. Drawdown [%]                   -3.821017
Avg. Drawdown [%]                   -0.364002
Max. Drawdown Duration       75 days 11:00:00
Avg. Drawdown Duration        4 days 21:00:00
# Trades                                   21
Win Rate [%]                        57.142857
Best Trade [%]                       4.426718
Worst Trade [%]                       -2.8439
Avg. Trade [%]                    

## MACD

### Ostre

In [25]:
class CustomStrategy(SignalStrategy):
    
    ssl = 0.0496
    ttp = 0.0514
    size_tr = 0.83
    def init(self):
        
        super().init()
        self.rsi = self.I(lambda x: data['MACD_decision'], 'macd')

    def next(self):
        
        close = self.data.Close
        signal = self.rsi
        #prev_signal = self.rsi[-1]
        
        upper_tp = close*(1+self.ttp) 
        upper_sl = close*(1+self.ssl) 
        lower_sl = close*(1-self.ssl)   
        lower_tp = close*(1-self.ttp)
        
        #size_transaction = 0.85
        
        #if not signal == prev_signal:
        if signal == 1 and not self.position.is_long:
            self.buy(size=self.size_tr, sl=lower_sl, tp=upper_tp)
        elif signal == -1 and not self.position.is_short:
            self.sell(size=self.size_tr, sl = upper_sl, tp=lower_tp)
                
bt = Backtest(data, CustomStrategy, cash=10000, commission=0.002, 
              trade_on_close=False, hedging=False)
stats = bt.run()
bt.plot()
stats

#optymalizacja parametrow
# stats_skopt, heatmap, optimize_result = bt.optimize(ttp=[0.01, 0.1],
#            ssl=[0.01, 0.1],
#            size_tr=[0.4, 1], 
#            maximize='Equity Final [$]',
#            method='skopt',
#            max_tries=1000,
#            random_state=10,
#            return_heatmap=True,
#            return_optimization=True)
# heatmap.sort_values().iloc[-3:]

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   99.826238
Equity Final [$]                  9598.288102
Equity Peak [$]                  10074.407019
Return [%]                          -4.017119
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                    -4.37421
Volatility (Ann.) [%]                3.143045
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                   -5.092934
Avg. Drawdown [%]                   -2.560469
Max. Drawdown Duration      266 days 11:00:00
Avg. Drawdown Duration      133 days 10:00:00
# Trades                                   76
Win Rate [%]                        44.736842
Best Trade [%]                       1.700345
Worst Trade [%]                      -2.71577
Avg. Trade [%]                    

In [21]:
stats_skopt

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   83.492615
Equity Final [$]                 10891.602079
Equity Peak [$]                  11014.450865
Return [%]                           8.916021
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                    9.764965
Volatility (Ann.) [%]                6.775731
Sharpe Ratio                         1.441168
Sortino Ratio                        2.472827
Calmar Ratio                         3.849479
Max. Drawdown [%]                   -2.536698
Avg. Drawdown [%]                   -0.560009
Max. Drawdown Duration       72 days 20:00:00
Avg. Drawdown Duration        7 days 11:00:00
# Trades                                   70
Win Rate [%]                        58.571429
Best Trade [%]                       1.097886
Worst Trade [%]                     -1.313999
Avg. Trade [%]                    

In [5]:
class CustomStrategy(SignalStrategy):
    
    ssl = 0.0496
    ttp = 0.0514
    size_tr = 0.83
    def init(self):
        
        super().init()
        self.rsi = self.I(lambda x: data['fuzz_MACD_strategy'], 'macd')

    def next(self):
        
        close = self.data.Close
        signal = self.rsi
        #prev_signal = self.rsi[-1]
        
        upper_tp = close*(1+self.ttp) 
        upper_sl = close*(1+self.ssl) 
        lower_sl = close*(1-self.ssl)   
        lower_tp = close*(1-self.ttp)
        
        #size_transaction = 0.85
        
        #if not signal == prev_signal:
        if signal == 1 and not self.position.is_long:
            self.buy(size=self.size_tr, sl=lower_sl, tp=upper_tp)
        elif signal == -1 and not self.position.is_short:
            self.sell(size=self.size_tr, sl = upper_sl, tp=lower_tp)
                
bt = Backtest(data, CustomStrategy, cash=10000, commission=0.002, 
              trade_on_close=False, hedging=False)
stats = bt.run()
bt.plot()
stats

#optymalizacja parametrow
# stats_skopt, heatmap, optimize_result = bt.optimize(ttp=[0.01, 0.1],
#            ssl=[0.01, 0.1],
#            size_tr=[0.4, 1], 
#            maximize='Equity Final [$]',
#            method='skopt',
#            max_tries=1000,
#            random_state=10,
#            return_heatmap=True,
#            return_optimization=True)
# heatmap.sort_values().iloc[-3:]

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   99.218071
Equity Final [$]                 10237.402712
Equity Peak [$]                  10357.798565
Return [%]                           2.374027
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                    2.592623
Volatility (Ann.) [%]                3.657656
Sharpe Ratio                         0.708821
Sortino Ratio                         1.15675
Calmar Ratio                         0.668215
Max. Drawdown [%]                   -3.879925
Avg. Drawdown [%]                   -0.706044
Max. Drawdown Duration      239 days 15:00:00
Avg. Drawdown Duration       26 days 06:00:00
# Trades                                   11
Win Rate [%]                        72.727273
Best Trade [%]                       4.256273
Worst Trade [%]                     -2.372362
Avg. Trade [%]                    

In [23]:
stats_skopt

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   98.262381
Equity Final [$]                  11250.39601
Equity Peak [$]                   11296.41675
Return [%]                           12.50396
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                   13.715438
Volatility (Ann.) [%]                7.386991
Sharpe Ratio                         1.856702
Sortino Ratio                         3.37136
Calmar Ratio                         3.091061
Max. Drawdown [%]                   -4.437129
Avg. Drawdown [%]                   -0.513116
Max. Drawdown Duration       70 days 07:00:00
Avg. Drawdown Duration        5 days 16:00:00
# Trades                                    5
Win Rate [%]                            100.0
Best Trade [%]                       6.736848
Worst Trade [%]                      0.528245
Avg. Trade [%]                    

## Bollinger Bands 

### Ostre

In [27]:
class CustomStrategy(SignalStrategy):
    
    ssl = 0.0496
    ttp = 0.0514
    size_tr = 0.83
    def init(self):
        
        super().init()
        self.rsi = self.I(lambda x: data['dec_bollinger'], 'bollinger')

    def next(self):
        
        close = self.data.Close
        signal = self.rsi
        #prev_signal = self.rsi[-1]
        
        upper_tp = close*(1+self.ttp) 
        upper_sl = close*(1+self.ssl) 
        lower_sl = close*(1-self.ssl)   
        lower_tp = close*(1-self.ttp)
        
        #size_transaction = 0.85
        
        #if not signal == prev_signal:
        if signal == 1 and not self.position.is_long:
            self.buy(size=self.size_tr, sl=lower_sl, tp=upper_tp)
        elif signal == -1 and not self.position.is_short:
            self.sell(size=self.size_tr, sl = upper_sl, tp=lower_tp)
                
bt = Backtest(data, CustomStrategy, cash=10000, commission=0.002, 
              trade_on_close=False, hedging=False)
stats = bt.run()
bt.plot()
stats

#optymalizacja parametrow
# stats_skopt, heatmap, optimize_result = bt.optimize(ttp=[0.01, 0.1],
#            ssl=[0.01, 0.1],
#            size_tr=[0.4, 1], 
#            maximize='Equity Final [$]',
#            method='skopt',
#            max_tries=1000,
#            random_state=10,
#            return_heatmap=True,
#            return_optimization=True)
# heatmap.sort_values().iloc[-3:]

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   98.783666
Equity Final [$]                  9594.893964
Equity Peak [$]                       10000.0
Return [%]                           -4.05106
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                   -4.411099
Volatility (Ann.) [%]                3.493535
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                   -5.528118
Avg. Drawdown [%]                   -5.528118
Max. Drawdown Duration      263 days 11:00:00
Avg. Drawdown Duration      263 days 11:00:00
# Trades                                   32
Win Rate [%]                           21.875
Best Trade [%]                       1.475182
Worst Trade [%]                     -3.344577
Avg. Trade [%]                    

In [25]:
stats_skopt

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   89.574283
Equity Final [$]                  9870.212566
Equity Peak [$]                       10000.0
Return [%]                          -1.297874
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                   -1.415024
Volatility (Ann.) [%]                 2.68791
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                   -3.094545
Avg. Drawdown [%]                   -3.094545
Max. Drawdown Duration      263 days 11:00:00
Avg. Drawdown Duration      263 days 11:00:00
# Trades                                   35
Win Rate [%]                        28.571429
Best Trade [%]                       2.003123
Worst Trade [%]                      -2.39716
Avg. Trade [%]                    

### Rozmyte

In [28]:
class CustomStrategy(SignalStrategy):
    
    ssl = 0.0496
    ttp = 0.0514
    size_tr = 0.83
    def init(self):
        
        super().init()
        self.rsi = self.I(lambda x: data['fuzz_BB_strategy'], 'bollinger')

    def next(self):
        
        close = self.data.Close
        signal = self.rsi
        #prev_signal = self.rsi[-1]
        
        upper_tp = close*(1+self.ttp) 
        upper_sl = close*(1+self.ssl) 
        lower_sl = close*(1-self.ssl)   
        lower_tp = close*(1-self.ttp)
        
        #size_transaction = 0.85
        
        #if not signal == prev_signal:
        if signal == 1 and not self.position.is_long:
            self.buy(size=self.size_tr, sl=lower_sl, tp=upper_tp)
        elif signal == -1 and not self.position.is_short:
            self.sell(size=self.size_tr, sl = upper_sl, tp=lower_tp)
                
bt = Backtest(data, CustomStrategy, cash=10000, commission=0.002, 
              trade_on_close=False, hedging=False)
stats = bt.run()
bt.plot()
stats

#optymalizacja parametrow
# stats_skopt, heatmap, optimize_result = bt.optimize(ttp=[0.01, 0.1],
#            ssl=[0.01, 0.1],
#            size_tr=[0.4, 1], 
#            maximize='Equity Final [$]',
#            method='skopt',
#            max_tries=1000,
#            random_state=10,
#            return_heatmap=True,
#            return_optimization=True)
# heatmap.sort_values().iloc[-3:]

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   98.783666
Equity Final [$]                  9591.556689
Equity Peak [$]                  10085.171092
Return [%]                          -4.084433
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                   -4.447368
Volatility (Ann.) [%]                3.825263
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                   -5.960282
Avg. Drawdown [%]                   -1.330623
Max. Drawdown Duration      205 days 15:00:00
Avg. Drawdown Duration       32 days 21:00:00
# Trades                                   21
Win Rate [%]                        23.809524
Best Trade [%]                       1.310019
Worst Trade [%]                     -2.707524
Avg. Trade [%]                    

In [27]:
stats_skopt

Start                     2023-01-04 14:00:00
End                       2023-09-29 17:00:00
Duration                    268 days 03:00:00
Exposure Time [%]                   85.664639
Equity Final [$]                 10867.934356
Equity Peak [$]                  10932.746836
Return [%]                           8.679344
Buy & Hold Return [%]               -0.322416
Return (Ann.) [%]                    9.504785
Volatility (Ann.) [%]                 6.44965
Sharpe Ratio                          1.47369
Sortino Ratio                        2.469345
Calmar Ratio                         2.374631
Max. Drawdown [%]                   -4.002636
Avg. Drawdown [%]                   -0.499396
Max. Drawdown Duration       72 days 19:00:00
Avg. Drawdown Duration        5 days 21:00:00
# Trades                                   12
Win Rate [%]                        83.333333
Best Trade [%]                       3.178625
Worst Trade [%]                     -2.647433
Avg. Trade [%]                    